In [1]:
#Classification Stock Prices  with Keras LTSM Network

from pandas import read_csv
from pandas import datetime
from math import sqrt
from matplotlib import pyplot
import numpy as np
import pandas as pd
from pandas_datareader import data as wb
from pandas import DataFrame
from pandas import Series
from pandas import concat
from pandas import read_csv
from pandas import datetime
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import LSTM
from math import sqrt
from matplotlib import pyplot
from sklearn.model_selection import train_test_split
import library as mio
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import SGDClassifier
from sklearn import neighbors
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.grid_search import GridSearchCV
from sklearn.metrics import make_scorer
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score, classification_report, roc_auc_score, matthews_corrcoef
from sklearn.tree import DecisionTreeClassifier
from sklearn.cross_validation import cross_val_score

from sklearn.metrics import classification_report
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import VotingClassifier
from sklearn.cross_validation import cross_val_predict
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LogisticRegression



Using TensorFlow backend.
j:\Anaconda3\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
j:\Anaconda3\lib\site-packages\sklearn\grid_search.py:42: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [2]:
# reduced list only the most correlated
indices_list_Complete = ["SPY","^IXIC", "^DJI", "^GDAXI", "^FTSE","^FCHI", "^N225","^HSI", "^AXJO","ORB", "EUR","AUD","GBP","JPY", "SILVER", "GOLD", "WT1010"] # reduced list only the most correlated
indice_target=["^GSPC"]

In [3]:
start_date = "2003-01-01" # Start day of Series
end_date = "2017-01-01"	  # Final day of series
dates = pd.date_range(start_date, end_date)  # date range as index

In [4]:
df_index = mio.get_data(indices_list_Complete, dates)
df_target= mio.get_data(indice_target, dates)

In [5]:
df_index.fillna(method='bfill', inplace=True)
df_target.fillna(method='bfill', inplace=True)

In [6]:
df_index.describe()

SPY        ^IXIC          ^DJI        ^GDAXI        ^FTSE  \
count  3525.000000  3525.000000   3525.000000   3525.000000  3525.000000   
mean    124.247170  2887.485241  12676.749688   6792.847443  5650.849134   
std      42.716304  1111.738679   3019.752104   2287.728860   879.576705   
min      57.440272  1268.640015   6547.049805   2202.959961  3287.000000   
25%      93.528227  2094.139893  10444.370117   4998.160156  5053.200195   
50%     112.113904  2480.330078  12105.549805   6534.970215  5808.799805   
75%     152.589273  3496.429932  15112.190430   8260.480469  6364.700195   
max     225.444643  5487.439941  19974.619141  12374.730469  7142.799805   

             ^FCHI         ^N225          ^HSI        ^AXJO          ORB  \
count  3525.000000   3525.000000   3525.000000  3525.000000  3525.000000   
mean   4130.124744  12944.451194  19392.780442  4716.324737    70.492837   
std     772.017335   3478.880031   4632.425945   855.962899    29.223703   
min    2403.040039   7054.979980   8409.009766  2700.399902    22.480000   
25%    3580.479980   9844.589844  15413.429688  4169.500000    45.250000   
50%    4038.699951  11944.299805  20672.390625  4807.399902    66.340000   
75%    4582.830078  16024.849609  22835.820312  5342.399902   101.890000   
max    6168.149902  20868.029297  31638.220703  6828.700195   140.730000   

               EUR          AUD          GBP          JPY       SILVER  \
count  3525.000000  3525.000000  3525.000000  3525.000000  3525.000000   
mean      0.784911     1.218466     0.605921   103.269039    16.829385   
std       0.073974     0.180926     0.066218    13.772426     8.778454   
min       0.625360     0.906698     0.474330    75.751979     4.370000   
25%       0.734626     1.071435     0.550249    92.727524    10.770000   
50%       0.772966     1.237935     0.616478   105.553327    15.860000   
75%       0.829636     1.341054     0.643910   115.820209    20.020000   
max       0.963904     1.776110     0.822470   125.630900    48.700000   

              GOLD       WT1010  
count  3525.000000  3525.000000  
mean    993.989504     2.667827  
std     427.903735     1.383519  
min     319.750000    -0.200000  
25%     611.250000     1.520000  
50%    1081.100000     3.150000  
75%    1308.250000     3.910000  
max    1891.000000     4.690000

In [7]:
colums_1=df_index.columns

In [8]:
for index in colums_1:
    df_index[index+'_Ret'] = df_index[index].pct_change(1)
    df_index.drop(index,axis=1, inplace=True)

In [9]:
df_index.replace([np.inf, -np.inf], np.nan)
df_index[df_index==np.inf] = np.nan
df_index[df_index==-np.inf] = np.nan
df_index.fillna(method='bfill', inplace=True)

In [10]:
df_index.describe()

SPY_Ret    ^IXIC_Ret     ^DJI_Ret   ^GDAXI_Ret    ^FTSE_Ret  \
count  3525.000000  3525.000000  3525.000000  3525.000000  3525.000000   
mean      0.000405     0.000472     0.000296     0.000471     0.000231   
std       0.011829     0.013110     0.011018     0.014207     0.011625   
min      -0.098448    -0.091424    -0.078733    -0.074472    -0.088483   
25%      -0.004187    -0.005483    -0.004262    -0.006168    -0.005039   
50%       0.000730     0.000928     0.000505     0.000837     0.000307   
75%       0.005602     0.006871     0.005288     0.007436     0.005789   
max       0.145198     0.118059     0.110803     0.114020     0.098387   

         ^FCHI_Ret    ^N225_Ret     ^HSI_Ret    ^AXJO_Ret      ORB_Ret  \
count  3525.000000  3525.000000  3525.000000  3525.000000  3525.000000   
mean      0.000220     0.000341     0.000359     0.000236     0.000321   
std       0.014227     0.015348     0.014816     0.010559     0.017367   
min      -0.090368    -0.114064    -0.136666    -0.097524    -0.084716   
25%      -0.006589    -0.006627    -0.005922    -0.004710    -0.008782   
50%       0.000340     0.000000     0.000000     0.000368     0.000543   
75%       0.007399     0.008219     0.007064     0.005665     0.009836   
max       0.111762     0.141503     0.143471     0.057896     0.136594   

           EUR_Ret      AUD_Ret      GBP_Ret      JPY_Ret   SILVER_Ret  \
count  3525.000000  3525.000000  3525.000000  3525.000000  3525.000000   
mean      0.000011    -0.000040     0.000089     0.000009     0.000604   
std       0.005865     0.007932     0.005748     0.005649     0.022397   
min      -0.031090    -0.049097    -0.031450    -0.036115    -0.170495   
25%      -0.003242    -0.004329    -0.003059    -0.003001    -0.010110   
50%      -0.000115    -0.000408    -0.000003     0.000026     0.000000   
75%       0.003206     0.003811     0.002998     0.003140     0.012328   
max       0.032361     0.096461     0.082558     0.031060     0.200557   

          GOLD_Ret   WT1010_Ret  
count  3525.000000  3525.000000  
mean      0.000420    -0.002273  
std       0.012036     0.183213  
min      -0.085271    -3.000000  
25%      -0.005659    -0.011538  
50%       0.000317     0.000000  
75%       0.006895     0.009804  
max       0.100255     4.000000

In [11]:
colums_2=df_target.columns

In [12]:
for index in colums_2:
    df_target[index+'_Ret'] = df_target[index].pct_change(1)
    df_target.drop(index,axis=1, inplace=True)

In [13]:
df_target.replace([np.inf, -np.inf], np.nan)
df_target[df_target==np.inf] = np.nan
df_target[df_target==-np.inf] = np.nan
df_target.fillna(method='bfill', inplace=True)

In [14]:
df_target.describe()

^GSPC_Ret
count  3525.000000
mean      0.000326
std       0.011888
min      -0.090350
25%      -0.004445
50%       0.000693
75%       0.005545
max       0.115800

In [15]:
df_final_1 = df_index.join(df_target)

In [16]:
df_final=df_final_1.copy()


In [17]:
def Label_Change2 (x):
    if x >= 0 :
        return 1

    return 0

In [18]:
df_final=df_final.applymap(Label_Change2)


In [19]:

columns=df_final.columns

In [20]:
values = df_final.values
train_size = int(len(values) * 0.66)
train, test = values[0:train_size], values[train_size:len(values)]
print('Observations: %d' % (len(values)))
print('Training Observations: %d' % (len(train)))
print('Testing Observations: %d' % (len(test)))

Observations: 3525
Training Observations: 2326
Testing Observations: 1199


In [21]:
df_test=df_final[train_size:len(values)]

In [22]:
indexs=df_test.index

In [23]:
indexs

DatetimeIndex(['2012-03-28', '2012-03-29', '2012-03-30', '2012-04-02',
               '2012-04-03', '2012-04-04', '2012-04-05', '2012-04-09',
               '2012-04-10', '2012-04-11',
               ...
               '2016-12-16', '2016-12-19', '2016-12-20', '2016-12-21',
               '2016-12-22', '2016-12-23', '2016-12-27', '2016-12-28',
               '2016-12-29', '2016-12-30'],
              dtype='datetime64[ns]', length=1199, freq=None)

In [24]:
# split into input and outputs
train_X, train_y = train[:, :-1], train[:, -1]
test_X, test_y = test[:, :-1], test[:, -1]
# reshape input to be 3D [samples, timesteps, features]



In [25]:
test_y

array([0, 0, 1, ..., 0, 0, 0], dtype=int64)

In [26]:
#train_XS = train_XS.reshape((train_XS.shape[0], 1, train_XS.shape[1]))
#test_XS = test_XS.reshape((test_XS.shape[0], 1, test_XS.shape[1]))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(2326, 17) (2326,) (1199, 17) (1199,)


In [39]:
#clf = neighbors.KNeighborsClassifier(algorithm='ball_tree', n_neighbors=300, weights='distance', leaf_size= 30)  
clf = neighbors.KNeighborsClassifier()  

In [40]:
clf.fit(train_X, train_y)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=5, p=2,
           weights='uniform')

In [41]:
accuracy = clf.score(test_X, test_y)
y_test_pred = clf.predict(test_X)
Sscore = f1_score(test_y, predictions)

In [42]:
from sklearn.metrics import confusion_matrix, classification_report


In [43]:
def pretty_confusion_matrix(y_true, y_pred, labels=["False", "True"]):
    cm = confusion_matrix(y_true, y_pred)
    pred_labels = ['Predicted '+ l for l in labels]
    df = pd.DataFrame(cm, index=labels, columns=pred_labels)
    return df

In [44]:
# check the confusion matrix, precision and recall

pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down'])

Predicted UP  Predicted Down
UP             533              31
Down            37             598

In [45]:
print(classification_report(test_y, y_test_pred))

             precision    recall  f1-score   support

          0       0.94      0.95      0.94       564
          1       0.95      0.94      0.95       635

avg / total       0.94      0.94      0.94      1199



In [106]:
#clf1 =RandomForestClassifier(n_estimators=500, criterion= 'gini',verbose=10)
clf1 =RandomForestClassifier()
print("Random Forest Binary Classification")

Random Forest Binary Classification


In [107]:
clf1.fit(train_X, train_y)
accuracy = clf1.score(test_X, test_y)
y_test_pred = clf1.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             535              29
Down            25             610
             precision    recall  f1-score   support

          0       0.96      0.95      0.95       564
          1       0.95      0.96      0.96       635

avg / total       0.95      0.95      0.95      1199

Accuracy: 0.9549624687239366
F1_score: 0.9576138147566718


In [108]:
accuracy = clf1.score(test_X, test_y)
y_test_pred = clf1.predict(test_X)
Sscore = f1_score(test_y, predictions)

In [104]:
#clf2 = SGDClassifier( alpha= 0.01,penalty='elasticnet', loss='perceptron', learning_rate= 'invscaling', eta0=0.2)
clf2 = SGDClassifier()
print("Stochastic Gradient Descent binary Classification")

Stochastic Gradient Descent binary Classification


In [105]:
clf2.fit(train_X, train_y)
accuracy = clf2.score(test_X, test_y)
y_test_pred = clf2.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             517              47
Down             6             629
             precision    recall  f1-score   support

          0       0.99      0.92      0.95       564
          1       0.93      0.99      0.96       635

avg / total       0.96      0.96      0.96      1199

Accuracy: 0.9557964970809008
F1_score: 0.9595728451563693


j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)


In [102]:
clf3 = SVC(C=2000,kernel= 'linear')
print("SVM binary Classification")

SVM binary Classification


In [103]:
clf3.fit(train_X, train_y)
accuracy = clf3.score(test_X, test_y)
y_test_pred = clf3.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             528              36
Down            17             618
             precision    recall  f1-score   support

          0       0.97      0.94      0.95       564
          1       0.94      0.97      0.96       635

avg / total       0.96      0.96      0.96      1199

Accuracy: 0.9557964970809008
F1_score: 0.9588828549262995


In [99]:
print("Ada Boosting binary Classification")

clf4 = AdaBoostClassifier()
#clf4 = AdaBoostClassifier(n_estimators=80, algorithm='SAMME.R', learning_rate= 0.7)

Ada Boosting binary Classification


In [101]:
clf4.fit(train_X, train_y)
accuracy = clf4.score(test_X, test_y)
y_test_pred = clf4.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             527              37
Down            17             618
             precision    recall  f1-score   support

          0       0.97      0.93      0.95       564
          1       0.94      0.97      0.96       635

avg / total       0.96      0.95      0.95      1199

Accuracy: 0.9549624687239366
F1_score: 0.9581395348837208


In [163]:
print("Gradient Tree Boosting binary Classification")
#{'learning_rate': 0.1, 'max_features': 'sqrt', 'min_samples_leaf': 40, 'min_samples_split': 200, 'n_estimators': 200}
#clf5 = GradientBoostingClassifier(min_samples_leaf=75, n_estimators=90, max_features= 'auto',min_samples_split=300, learning_rate=0.1)#
clf5 = GradientBoostingClassifier(min_samples_leaf=40, n_estimators=200, max_features= 'sqrt',min_samples_split=200, learning_rate=0.1)

Gradient Tree Boosting binary Classification


In [164]:
clf5.fit(train_X, train_y)
accuracy = clf5.score(test_X, test_y)
y_test_pred = clf5.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             531              33
Down            20             615
             precision    recall  f1-score   support

          0       0.96      0.94      0.95       564
          1       0.95      0.97      0.96       635

avg / total       0.96      0.96      0.96      1199

Accuracy: 0.9557964970809008
F1_score: 0.9586905689789555


In [119]:
print("Logistic Regresion Binary Classification")

clf6 = LogisticRegression() 
#clf6 = LogisticRegression(penalty= 'l2', C= 1, solver= 'liblinear') 

Logistic Regresion Binary Classification


In [120]:
clf6.fit(train_X, train_y)
accuracy = clf6.score(test_X, test_y)
y_test_pred = clf6.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             527              37
Down            17             618
             precision    recall  f1-score   support

          0       0.97      0.93      0.95       564
          1       0.94      0.97      0.96       635

avg / total       0.96      0.95      0.95      1199

Accuracy: 0.9549624687239366
F1_score: 0.9581395348837208


In [147]:
from sklearn.neural_network import MLPClassifier
print("MLPClassifier Classification")
# {'activation': 'relu', 'alpha': 0.0001, 'hidden_layer_sizes': (80, 2), 'learning_rate': 'constant'}
clf7 = MLPClassifier(shuffle =False,activation="relu",alpha=0.0001,hidden_layer_sizes=(80, 2), learning_rate='constant',max_iter =2500)  

MLPClassifier Classification


In [148]:
clf7.fit(train_X, train_y)
accuracy = clf7.score(test_X, test_y)
y_test_pred = clf7.predict(test_X)
Sscore = f1_score(test_y, y_test_pred)
print(pretty_confusion_matrix(test_y, y_test_pred, labels=['UP', 'Down']))
print(classification_report(test_y, y_test_pred))
print("Accuracy: {}\nF1_score: {}".format(accuracy,Sscore))

      Predicted UP  Predicted Down
UP             525              39
Down            18             617
             precision    recall  f1-score   support

          0       0.97      0.93      0.95       564
          1       0.94      0.97      0.96       635

avg / total       0.95      0.95      0.95      1199

Accuracy: 0.9524603836530442
F1_score: 0.9558481797056546


In [140]:
accu=make_scorer(accuracy_score)

In [141]:
parameters={'learning_rate': ["constant", "invscaling", "adaptive"],'hidden_layer_sizes': [(80,1), (80,2), (80,4), (80,10)],
             'alpha': [0.0001,0.001,0.01 ],'activation': ["logistic", "relu", "tanh","identity"]}
    
clf = GridSearchCV(MLPClassifier(shuffle=False,max_iter =500),  param_grid =  parameters, scoring=accu, verbose=100)
clf.fit(train_X, train_y)
df=pd.DataFrame(clf.grid_scores_)

Fitting 3 folds for each of 144 candidates, totalling 432 fits
[CV] activation=logistic, alpha=0.0001, hidden_layer_sizes=(80, 1), learning_rate=constant 


j:\Anaconda3\lib\site-packages\sklearn\neural_network\multilayer_perceptron.py:564: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


[CV]  activation=logistic, alpha=0.0001, hidden_layer_sizes=(80, 1), learning_rate=constant, score=0.925258 -   3.4s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    3.4s remaining:    0.0s
[CV] activation=logistic, alpha=0.0001, hidden_layer_sizes=(80, 1), learning_rate=constant 


j:\Anaconda3\lib\site-packages\sklearn\neural_network\multilayer_perceptron.py:564: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


[CV]  activation=logistic, alpha=0.0001, hidden_layer_sizes=(80, 1), learning_rate=constant, score=0.934278 -   3.4s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    6.9s remaining:    0.0s
[CV] activation=logistic, alpha=0.0001, hidden_layer_sizes=(80, 1), learning_rate=constant 


...

[CV]  activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=constant, score=0.934278 -   0.4s
[CV] activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=constant 
[CV]  activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=constant, score=0.934278 -   2.2s
[CV] activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=constant 
[CV]  activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=constant, score=0.963824 -   1.4s
[CV] activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=invscaling 
[CV]  activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=invscaling, score=0.923969 -   1.3s
[CV] activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=invscaling 
[CV]  activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=invscaling, score=0.931701 -   1.5s
[CV] activation=tanh, alpha=0.001, hidden_layer_sizes=(80, 2), learning_rate=invscal

[CV]  activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=invscaling, score=0.958656 -   2.1s
[CV] activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive 
[CV]  activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive, score=0.923969 -   1.3s
[CV] activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive 
[CV]  activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive, score=0.931701 -   0.8s
[CV] activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive 
[CV]  activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 2), learning_rate=adaptive, score=0.954780 -   1.2s
[CV] activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 4), learning_rate=constant 
[CV]  activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 4), learning_rate=constant, score=0.927835 -   0.8s
[CV] activation=tanh, alpha=0.01, hidden_layer_sizes=(80, 4), learning_rate=constant 
[CV]  activat

[CV]  activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=constant, score=0.936856 -   0.1s
[CV] activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=constant 
[CV]  activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=constant, score=0.961240 -   0.1s
[CV] activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling 
[CV]  activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling, score=0.932990 -   0.1s
[CV] activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling 
[CV]  activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling, score=0.932990 -   0.1s
[CV] activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling 
[CV]  activation=identity, alpha=0.0001, hidden_layer_sizes=(80, 4), learning_rate=invscaling, score=0.959948 -   0.2s
[CV] activation=identity, alpha=0.0

[CV]  activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=invscaling, score=0.959948 -   0.3s
[CV] activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive 
[CV]  activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive, score=0.935567 -   0.2s
[CV] activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive 
[CV]  activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive, score=0.934278 -   0.1s
[CV] activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive 
[CV]  activation=identity, alpha=0.001, hidden_layer_sizes=(80, 4), learning_rate=adaptive, score=0.961240 -   0.1s
[CV] activation=identity, alpha=0.001, hidden_layer_sizes=(80, 10), learning_rate=constant 
[CV]  activation=identity, alpha=0.001, hidden_layer_sizes=(80, 10), learning_rate=constant, score=0.934278 -   0.2s
[CV] activation=identity, alpha=0.001, hidden_layer_

[CV]  activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=constant, score=0.934278 -   0.1s
[CV] activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=constant 
[CV]  activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=constant, score=0.936856 -   0.2s
[CV] activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=constant 
[CV]  activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=constant, score=0.959948 -   0.0s
[CV] activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=invscaling 
[CV]  activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=invscaling, score=0.935567 -   0.0s
[CV] activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=invscaling 
[CV]  activation=identity, alpha=0.01, hidden_layer_sizes=(80, 10), learning_rate=invscaling, score=0.935567 -   0.1s
[CV] activation=identity, alpha=0.01, hidden_lay

In [152]:
df.head()

parameters  mean_validation_score  \
0  {'activation': 'logistic', 'alpha': 0.0001, 'h...               0.939811   
1  {'activation': 'logistic', 'alpha': 0.0001, 'h...               0.938521   
2  {'activation': 'logistic', 'alpha': 0.0001, 'h...               0.938521   
3  {'activation': 'logistic', 'alpha': 0.0001, 'h...               0.938521   
4  {'activation': 'logistic', 'alpha': 0.0001, 'h...               0.940671   

                                cv_validation_scores  
0  [0.9252577319587629, 0.9342783505154639, 0.959...  
1  [0.9252577319587629, 0.9304123711340206, 0.959...  
2  [0.9252577319587629, 0.9317010309278351, 0.958...  
3  [0.9291237113402062, 0.9291237113402062, 0.957...  
4  [0.9278350515463918, 0.9329896907216495, 0.961...

In [149]:
clf.best_params_

{'activation': 'relu',
 'alpha': 0.0001,
 'hidden_layer_sizes': (80, 2),
 'learning_rate': 'constant'}

In [160]:
param_test1 = {'n_estimators':[20,40,50,60,70,80,90,100,150,200],'learning_rate':[0.1,0.2], 'min_samples_split':[100,200,300],'min_samples_leaf':[10,30,40, 50, 75],'max_features':['auto', 'sqrt']} 
clf2 = GridSearchCV(GradientBoostingClassifier(), param_grid = param_test1, scoring=accu,n_jobs=1,iid=False, cv=5, verbose=100)
clf2.fit(train_X, train_y)
df1=pd.DataFrame(clf2.grid_scores_)

Fitting 5 folds for each of 600 candidates, totalling 3000 fits
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20, score=0.929185 -   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20, score=0.912017 -   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=20, score=0.922747 -   0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.

[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80, score=0.914163 -   0.0s
[Parallel(n_jobs=1)]: Done  27 out of  27 | elapsed:    2.2s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80, score=0.922747 -   0.1s
[Parallel(n_jobs=1)]: Done  28 out of  28 | elapsed:    2.3s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80, score=0.963362 -   0.0s
[Parallel(n_jobs=1)]: Done  29 out of  29 | elapsed:    2.5s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=100, n_estimators=80 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=

[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40, score=0.944206 -   0.0s
[Parallel(n_jobs=1)]: Done  56 out of  56 | elapsed:    7.4s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40, score=0.914163 -   0.0s
[Parallel(n_jobs=1)]: Done  57 out of  57 | elapsed:    7.4s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40, score=0.922747 -   0.0s
[Parallel(n_jobs=1)]: Done  58 out of  58 | elapsed:    7.5s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=40 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=

[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=90, score=0.963362 -   0.1s
[Parallel(n_jobs=1)]: Done  84 out of  84 | elapsed:   10.3s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=90 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=90, score=0.971983 -   0.0s
[Parallel(n_jobs=1)]: Done  85 out of  85 | elapsed:   10.4s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=100 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=100, score=0.939914 -   0.1s
[Parallel(n_jobs=1)]: Done  86 out of  86 | elapsed:   10.6s remaining:    0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=200, n_estimators=100 
[CV]  learning_rate=0.1, max_features=auto, min_samples_le

[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60, score=0.942060 -   0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60, score=0.914163 -   0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60, score=0.920601 -   0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60, score=0.963362 -   0.0s
[CV] learning_rate=0.1, max_features=auto, min_samples_leaf=10, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.1, max_features=auto, min_samples_leaf=10, min

...

[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60, score=0.922747 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60, score=0.920601 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60, score=0.961207 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=60, score=0.974138 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min_samples_split=300, n_estimators=70 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=50, min

[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=40, score=0.922747 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=40 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=40, score=0.965517 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=40 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=40, score=0.974138 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=50 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=50, score=0.948498 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=50 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min

[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=150, score=0.971983 -   0.1s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200, score=0.937768 -   0.1s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200, score=0.909871 -   0.1s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200, score=0.922747 -   0.1s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=100, n_estimators=200 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf

[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=90, score=0.922747 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=90 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=90, score=0.963362 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=90 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=90, score=0.965517 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=100 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=100, score=0.937768 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=200, n_estimators=100 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, 

[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70, score=0.912017 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70, score=0.922747 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70, score=0.965517 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=70, score=0.971983 -   0.0s
[CV] learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min_samples_split=300, n_estimators=80 
[CV]  learning_rate=0.2, max_features=sqrt, min_samples_leaf=75, min

In [161]:
clf2.best_params_

{'learning_rate': 0.1,
 'max_features': 'sqrt',
 'min_samples_leaf': 40,
 'min_samples_split': 200,
 'n_estimators': 200}

In [162]:
clf2.best_score_

0.9467274678111588

In [165]:
param_test1=[{'loss':['hinge', 'log', 'modified_huber', 'squared_hinge', 'perceptron'],
              'penalty':['none', 'l2', 'l1', 'elasticnet'],
               'learning_rate':['constant','optimal','invscaling'],
              'eta0':[0.1,0.2], 'alpha': [0.1, 0.01, 0.001, 0.0001, 0.00001, 0.000001, 0.0000001]}]
clf3 = GridSearchCV(SGDClassifier(), param_grid = param_test1, scoring=accu,n_jobs=1,iid=False, cv=5, verbose=100)
clf3.fit(train_X, train_y)
df2=pd.DataFrame(clf3.grid_scores_)

Fitting 5 folds for each of 840 candidates, totalling 4200 fits
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none, score=0.935622 -   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none, score=0.905579 -   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none, score=0.903433 -   0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=hinge, penalty=none, score=0.9612

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc

[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=l1, score=0.943966 -   0.0s
[Parallel(n_jobs=1)]: Done  54 out of  54 | elapsed:    0.1s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=l1 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=l1, score=0.974138 -   0.0s
[Parallel(n_jobs=1)]: Done  55 out of  55 | elapsed:    0.1s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=elasticnet 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=elasticnet, score=0.952790 -   0.0s
[Parallel(n_jobs=1)]: Done  56 out of  56 | elapsed:    0.1s remaining:    0.0s
[CV] alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=elasticnet 
[CV]  alpha=0.1, eta0=0.1, learning_rate=constant, loss=modified_huber, penalty=elasticnet, score=0.866953 -   0.0s
[Parallel(n_jobs=1)]: Done  57 out of  57 | ela

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc

...

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc


[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l2, score=0.907725 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l2, score=0.959052 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l2, score=0.961207 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1, score=0.935622 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1, score=0.924893 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=log, penalty=l1, score=0.909871 -   0.0s
[CV] alpha=1e

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc


[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2, score=0.907725 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2, score=0.920601 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2, score=0.952586 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l2, score=0.941810 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l1 
[CV]  alpha=1e-07, eta0=0.2, learning_rate=invscaling, loss=perceptron, penalty=l1, score=0.946352 -   0.0s
[CV] alpha=1e-07, eta0=0.2, learning_rate=in

j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)
j:\Anaconda3\lib\site-packages\sklearn\linear_model\stoc

In [167]:
clf3.best_params_

{'alpha': 0.01,
 'eta0': 0.2,
 'learning_rate': 'optimal',
 'loss': 'hinge',
 'penalty': 'l1'}

In [168]:
clf3.best_score_

0.9462945833949978

In [169]:
df2.head()

parameters  mean_validation_score  \
0  {'alpha': 0.1, 'eta0': 0.1, 'learning_rate': '...               0.935134   
1  {'alpha': 0.1, 'eta0': 0.1, 'learning_rate': '...               0.898605   
2  {'alpha': 0.1, 'eta0': 0.1, 'learning_rate': '...               0.937720   
3  {'alpha': 0.1, 'eta0': 0.1, 'learning_rate': '...               0.941143   
4  {'alpha': 0.1, 'eta0': 0.1, 'learning_rate': '...               0.940284   

                                cv_validation_scores  
0  [0.9356223175965666, 0.9055793991416309, 0.903...  
1  [0.9527896995708155, 0.8776824034334764, 0.787...  
2  [0.927038626609442, 0.9012875536480687, 0.9163...  
3  [0.9527896995708155, 0.8991416309012875, 0.922...  
4  [0.944206008583691, 0.9055793991416309, 0.9206...

In [171]:
param_grid = [{'n_estimators':[20,40,50,60,70,80,90,100,150,200],'algorithm' : ['SAMME', 'SAMME.R'], 'learning_rate':[0.1, 0.3,0.5,0.7,1] }]


DTC = DecisionTreeClassifier(random_state = 11, max_features = "auto", class_weight = "balanced")

ABC = AdaBoostClassifier(base_estimator = DTC)


clf4 = GridSearchCV(ABC, param_grid=param_grid, scoring=accu, verbose=100 )
clf4.fit(train_X, train_y)
df3=pd.DataFrame(clf4.grid_scores_)

Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] algorithm=SAMME, learning_rate=0.1, n_estimators=20 .............
[CV]  algorithm=SAMME, learning_rate=0.1, n_estimators=20, score=0.921392 -   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.1, n_estimators=20 .............
[CV]  algorithm=SAMME, learning_rate=0.1, n_estimators=20, score=0.935567 -   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.1, n_estimators=20 .............
[CV]  algorithm=SAMME, learning_rate=0.1, n_estimators=20, score=0.939276 -   0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.1, n_estimators=40 .............
[CV]  algorithm=SAMME, learning_rate=0.1, n_estimators=40, score=0.917526 -   0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.2s remaining:    0.0s
[

[CV]  algorithm=SAMME, learning_rate=0.3, n_estimators=40, score=0.937984 -   0.0s
[Parallel(n_jobs=1)]: Done  36 out of  36 | elapsed:    6.9s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.3, n_estimators=50 .............
[CV]  algorithm=SAMME, learning_rate=0.3, n_estimators=50, score=0.912371 -   0.0s
[Parallel(n_jobs=1)]: Done  37 out of  37 | elapsed:    7.1s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.3, n_estimators=50 .............
[CV]  algorithm=SAMME, learning_rate=0.3, n_estimators=50, score=0.939433 -   0.0s
[Parallel(n_jobs=1)]: Done  38 out of  38 | elapsed:    7.2s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.3, n_estimators=50 .............
[CV]  algorithm=SAMME, learning_rate=0.3, n_estimators=50, score=0.936693 -   0.0s
[Parallel(n_jobs=1)]: Done  39 out of  39 | elapsed:    7.3s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.3, n_estimators=60 .............
[CV]  algorithm=SAMME, learning_rate=0.3, n_estimators=60, score

[CV]  algorithm=SAMME, learning_rate=0.5, n_estimators=60, score=0.922481 -   0.1s
[Parallel(n_jobs=1)]: Done  72 out of  72 | elapsed:   13.2s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.5, n_estimators=70 .............
[CV]  algorithm=SAMME, learning_rate=0.5, n_estimators=70, score=0.918814 -   0.0s
[Parallel(n_jobs=1)]: Done  73 out of  73 | elapsed:   13.3s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.5, n_estimators=70 .............
[CV]  algorithm=SAMME, learning_rate=0.5, n_estimators=70, score=0.927835 -   0.0s
[Parallel(n_jobs=1)]: Done  74 out of  74 | elapsed:   13.4s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.5, n_estimators=70 .............
[CV]  algorithm=SAMME, learning_rate=0.5, n_estimators=70, score=0.939276 -   0.1s
[Parallel(n_jobs=1)]: Done  75 out of  75 | elapsed:   13.6s remaining:    0.0s
[CV] algorithm=SAMME, learning_rate=0.5, n_estimators=80 .............
[CV]  algorithm=SAMME, learning_rate=0.5, n_estimators=80, score

[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=90, score=0.943152 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=100 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=100, score=0.907216 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=100 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=100, score=0.920103 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=100 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=100, score=0.935401 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=150 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=150, score=0.917526 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=150 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=150, score=0.932990 -   0.0s
[CV] algorithm=SAMME, learning_rate=0.7, n_estimators=150 ............
[CV]  algorithm=SAMME, learning_rate=0.7, n_estimators=150, score=0.930

[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=80, score=0.914948 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=80 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=80, score=0.930412 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=80 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=80, score=0.941860 -   0.2s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=90 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=90, score=0.913660 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=90 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=90, score=0.927835 -   0.2s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=90 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=90, score=0.941860 -   0.2s
[CV] algorithm=SAMME.R, learning_rate=0.1, n_estimators=100 ..........
[CV]  algorithm=SAMME.R, learning_rate=0.1, n_estimators=100, sc

[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=60, score=0.912371 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=60 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=60, score=0.932990 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=60 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=60, score=0.945736 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=70 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=70, score=0.913660 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=70 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=70, score=0.927835 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=70 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=70, score=0.937984 -   0.1s
[CV] algorithm=SAMME.R, learning_rate=0.5, n_estimators=80 ...........
[CV]  algorithm=SAMME.R, learning_rate=0.5, n_estimators=80, sco

[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=40, score=0.903351 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=40 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=40, score=0.921392 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=40 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=40, score=0.918605 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=50 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=50, score=0.911082 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=50 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=50, score=0.929124 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=50 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=50, score=0.923773 -   0.0s
[CV] algorithm=SAMME.R, learning_rate=1, n_estimators=60 .............
[CV]  algorithm=SAMME.R, learning_rate=1, n_estimators=60, score=0.912371 - 

In [172]:
clf4.best_params_

{'algorithm': 'SAMME.R', 'learning_rate': 0.5, 'n_estimators': 80}

In [173]:
clf4.best_score_

0.9342218400687876

In [174]:
params_map = [{ 'C': [0.001,0.005, 0.01,0.02, 0.1,0.4, 0.5,0.6,0.7, 1.0, 2.0, 5.0, 10.0, 100.0],'kernel': ['rbf'],'gamma': ['auto',0.001,0.01, 0.05,0.1, 0.5, 1.0,4.0, 5.0, 6.0, 10.0,50.0,100.0,150.0]},
    {'kernel': ['linear'], 'C': [1, 10, 100, 1000, 1500, 2000, 2500,3000, 3500,4000]},
    #{'kernel': ['poly'], 'C': [1, 10, 100, 1000, 1500, 2000, 2500,3000, 3500,4000],'degree':[2,3,4,5,6,7,8,9,10,15], 'gamma': ['auto',0.001,0.01, 0.05,0.1, 0.5, 1.0, 5.0]},
    {'kernel': ['sigmoid'], 'C': [1, 10, 100, 1000, 1500, 2000, 2500,3000, 3500,4000], 'gamma': ['auto',0.001,0.01, 0.05,0.1, 0.5, 1.0, 5.0]}]


clf5 = GridSearchCV(SVC(), params_map, scoring=accu, verbose=100)
clf5.fit(train_X, train_y)
df4=pd.DataFrame(clf5.grid_scores_)


Fitting 3 folds for each of 286 candidates, totalling 858 fits
[CV] C=0.001, gamma=auto, kernel=rbf .................................
[CV] ........ C=0.001, gamma=auto, kernel=rbf, score=0.551546 -   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] C=0.001, gamma=auto, kernel=rbf .................................
[CV] ........ C=0.001, gamma=auto, kernel=rbf, score=0.551546 -   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.2s remaining:    0.0s
[CV] C=0.001, gamma=auto, kernel=rbf .................................
[CV] ........ C=0.001, gamma=auto, kernel=rbf, score=0.551680 -   0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.3s remaining:    0.0s
[CV] C=0.001, gamma=0.001, kernel=rbf ................................
[CV] ....... C=0.001, gamma=0.001, kernel=rbf, score=0.551546 -   0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.4s remaining:    0.0s
[CV] C=0.001, gamma=0.001, kernel=rbf ...........

[CV] ....... C=0.001, gamma=100.0, kernel=rbf, score=0.551546 -   0.1s
[Parallel(n_jobs=1)]: Done  38 out of  38 | elapsed:    5.3s remaining:    0.0s
[CV] C=0.001, gamma=100.0, kernel=rbf ................................
[CV] ....... C=0.001, gamma=100.0, kernel=rbf, score=0.551680 -   0.1s
[Parallel(n_jobs=1)]: Done  39 out of  39 | elapsed:    5.4s remaining:    0.0s
[CV] C=0.001, gamma=150.0, kernel=rbf ................................
[CV] ....... C=0.001, gamma=150.0, kernel=rbf, score=0.551546 -   0.1s
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    5.7s remaining:    0.0s
[CV] C=0.001, gamma=150.0, kernel=rbf ................................
[CV] ....... C=0.001, gamma=150.0, kernel=rbf, score=0.551546 -   0.1s
[Parallel(n_jobs=1)]: Done  41 out of  41 | elapsed:    5.9s remaining:    0.0s
[CV] C=0.001, gamma=150.0, kernel=rbf ................................
[CV] ....... C=0.001, gamma=150.0, kernel=rbf, score=0.551680 -   0.1s
[Parallel(n_jobs=1)]: Done  42 out of  42

[CV] ........ C=0.005, gamma=50.0, kernel=rbf, score=0.551546 -   0.0s
[Parallel(n_jobs=1)]: Done  76 out of  76 | elapsed:   10.6s remaining:    0.0s
[CV] C=0.005, gamma=50.0, kernel=rbf .................................
[CV] ........ C=0.005, gamma=50.0, kernel=rbf, score=0.551546 -   0.0s
[Parallel(n_jobs=1)]: Done  77 out of  77 | elapsed:   10.7s remaining:    0.0s
[CV] C=0.005, gamma=50.0, kernel=rbf .................................
[CV] ........ C=0.005, gamma=50.0, kernel=rbf, score=0.551680 -   0.0s
[Parallel(n_jobs=1)]: Done  78 out of  78 | elapsed:   10.9s remaining:    0.0s
[CV] C=0.005, gamma=100.0, kernel=rbf ................................
[CV] ....... C=0.005, gamma=100.0, kernel=rbf, score=0.551546 -   0.1s
[Parallel(n_jobs=1)]: Done  79 out of  79 | elapsed:   11.1s remaining:    0.0s
[CV] C=0.005, gamma=100.0, kernel=rbf ................................
[CV] ....... C=0.005, gamma=100.0, kernel=rbf, score=0.551546 -   0.1s
[Parallel(n_jobs=1)]: Done  80 out of  80

[CV] ........ C=0.01, gamma=100.0, kernel=rbf, score=0.551546 -   0.1s
[CV] C=0.01, gamma=100.0, kernel=rbf .................................
[CV] ........ C=0.01, gamma=100.0, kernel=rbf, score=0.551546 -   0.1s
[CV] C=0.01, gamma=100.0, kernel=rbf .................................
[CV] ........ C=0.01, gamma=100.0, kernel=rbf, score=0.551680 -   0.1s
[CV] C=0.01, gamma=150.0, kernel=rbf .................................
[CV] ........ C=0.01, gamma=150.0, kernel=rbf, score=0.551546 -   0.1s
[CV] C=0.01, gamma=150.0, kernel=rbf .................................
[CV] ........ C=0.01, gamma=150.0, kernel=rbf, score=0.551546 -   0.1s
[CV] C=0.01, gamma=150.0, kernel=rbf .................................
[CV] ........ C=0.01, gamma=150.0, kernel=rbf, score=0.551680 -   0.1s
[CV] C=0.02, gamma=auto, kernel=rbf ..................................
[CV] ......... C=0.02, gamma=auto, kernel=rbf, score=0.942010 -   0.0s
[CV] C=0.02, gamma=auto, kernel=rbf ..................................
[CV] .

[CV] ........... C=0.1, gamma=0.1, kernel=rbf, score=0.912371 -   0.0s
[CV] C=0.1, gamma=0.1, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=0.1, kernel=rbf, score=0.927835 -   0.0s
[CV] C=0.1, gamma=0.1, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=0.1, kernel=rbf, score=0.963824 -   0.0s
[CV] C=0.1, gamma=0.5, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=0.5, kernel=rbf, score=0.942010 -   0.0s
[CV] C=0.1, gamma=0.5, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=0.5, kernel=rbf, score=0.931701 -   0.0s
[CV] C=0.1, gamma=0.5, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=0.5, kernel=rbf, score=0.963824 -   0.0s
[CV] C=0.1, gamma=1.0, kernel=rbf ....................................
[CV] ........... C=0.1, gamma=1.0, kernel=rbf, score=0.771907 -   0.0s
[CV] C=0.1, gamma=1.0, kernel=rbf ....................................
[CV] .

...

[CV] ................... C=100, kernel=linear, score=0.912371 -   0.0s
[CV] C=100, kernel=linear ............................................
[CV] ................... C=100, kernel=linear, score=0.931701 -   0.1s
[CV] C=100, kernel=linear ............................................
[CV] ................... C=100, kernel=linear, score=0.963824 -   0.1s
[CV] C=1000, kernel=linear ...........................................
[CV] .................. C=1000, kernel=linear, score=0.912371 -   1.0s
[CV] C=1000, kernel=linear ...........................................
[CV] .................. C=1000, kernel=linear, score=0.931701 -   1.0s
[CV] C=1000, kernel=linear ...........................................
[CV] .................. C=1000, kernel=linear, score=0.963824 -   1.6s
[CV] C=1500, kernel=linear ...........................................
[CV] .................. C=1500, kernel=linear, score=0.912371 -   1.5s
[CV] C=1500, kernel=linear ...........................................
[CV] .

[CV] ........ C=10, gamma=0.1, kernel=sigmoid, score=0.897933 -   0.0s
[CV] C=10, gamma=0.5, kernel=sigmoid .................................
[CV] ........ C=10, gamma=0.5, kernel=sigmoid, score=0.480670 -   0.0s
[CV] C=10, gamma=0.5, kernel=sigmoid .................................
[CV] ........ C=10, gamma=0.5, kernel=sigmoid, score=0.463918 -   0.0s
[CV] C=10, gamma=0.5, kernel=sigmoid .................................
[CV] ........ C=10, gamma=0.5, kernel=sigmoid, score=0.456072 -   0.0s
[CV] C=10, gamma=1.0, kernel=sigmoid .................................
[CV] ........ C=10, gamma=1.0, kernel=sigmoid, score=0.453608 -   0.0s
[CV] C=10, gamma=1.0, kernel=sigmoid .................................
[CV] ........ C=10, gamma=1.0, kernel=sigmoid, score=0.447165 -   0.0s
[CV] C=10, gamma=1.0, kernel=sigmoid .................................
[CV] ........ C=10, gamma=1.0, kernel=sigmoid, score=0.436693 -   0.0s
[CV] C=10, gamma=5.0, kernel=sigmoid .................................
[CV] .

[CV] .... C=1500, gamma=0.001, kernel=sigmoid, score=0.963824 -   0.2s
[CV] C=1500, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.01, kernel=sigmoid, score=0.923969 -   0.0s
[CV] C=1500, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.01, kernel=sigmoid, score=0.931701 -   0.0s
[CV] C=1500, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.01, kernel=sigmoid, score=0.947028 -   0.0s
[CV] C=1500, gamma=0.05, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.05, kernel=sigmoid, score=0.914948 -   0.0s
[CV] C=1500, gamma=0.05, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.05, kernel=sigmoid, score=0.898196 -   0.0s
[CV] C=1500, gamma=0.05, kernel=sigmoid ..............................
[CV] ..... C=1500, gamma=0.05, kernel=sigmoid, score=0.925065 -   0.0s
[CV] C=1500, gamma=0.1, kernel=sigmoid ...............................
[CV] .

[CV] ...... C=2500, gamma=0.5, kernel=sigmoid, score=0.480670 -   0.0s
[CV] C=2500, gamma=0.5, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=0.5, kernel=sigmoid, score=0.463918 -   0.0s
[CV] C=2500, gamma=0.5, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=0.5, kernel=sigmoid, score=0.456072 -   0.0s
[CV] C=2500, gamma=1.0, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=1.0, kernel=sigmoid, score=0.454897 -   0.0s
[CV] C=2500, gamma=1.0, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=1.0, kernel=sigmoid, score=0.448454 -   0.0s
[CV] C=2500, gamma=1.0, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=1.0, kernel=sigmoid, score=0.437984 -   0.0s
[CV] C=2500, gamma=5.0, kernel=sigmoid ...............................
[CV] ...... C=2500, gamma=5.0, kernel=sigmoid, score=0.456186 -   0.0s
[CV] C=2500, gamma=5.0, kernel=sigmoid ...............................
[CV] .

[CV] .... C=4000, gamma=0.001, kernel=sigmoid, score=0.912371 -   1.0s
[CV] C=4000, gamma=0.001, kernel=sigmoid .............................
[CV] .... C=4000, gamma=0.001, kernel=sigmoid, score=0.931701 -   0.5s
[CV] C=4000, gamma=0.001, kernel=sigmoid .............................
[CV] .... C=4000, gamma=0.001, kernel=sigmoid, score=0.963824 -   0.3s
[CV] C=4000, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=4000, gamma=0.01, kernel=sigmoid, score=0.916237 -   0.0s
[CV] C=4000, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=4000, gamma=0.01, kernel=sigmoid, score=0.921392 -   0.0s
[CV] C=4000, gamma=0.01, kernel=sigmoid ..............................
[CV] ..... C=4000, gamma=0.01, kernel=sigmoid, score=0.939276 -   0.0s
[CV] C=4000, gamma=0.05, kernel=sigmoid ..............................
[CV] ..... C=4000, gamma=0.05, kernel=sigmoid, score=0.921392 -   0.0s
[CV] C=4000, gamma=0.05, kernel=sigmoid ..............................
[CV] .

In [175]:
clf5.best_params_

{'C': 0.02, 'gamma': 'auto', 'kernel': 'rbf'}

In [176]:
clf5.best_score_

0.945829750644884

In [177]:
tuned_parameters = [{'n_estimators': [500,1000,2000,2500,3000,3500,4000, 4500,5000],
    'criterion':['gini','entropy'] }]

clf6 = GridSearchCV(RandomForestClassifier(), tuned_parameters, scoring=accu, verbose=100)
clf6.fit(train_X, train_y)
df5=pd.DataFrame(clf6.grid_scores_)

Fitting 3 folds for each of 18 candidates, totalling 54 fits
[CV] criterion=gini, n_estimators=500 ................................
[CV] ....... criterion=gini, n_estimators=500, score=0.918814 -   0.8s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.8s remaining:    0.0s
[CV] criterion=gini, n_estimators=500 ................................
[CV] ....... criterion=gini, n_estimators=500, score=0.934278 -   0.7s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    1.6s remaining:    0.0s
[CV] criterion=gini, n_estimators=500 ................................
[CV] ....... criterion=gini, n_estimators=500, score=0.948320 -   0.7s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    2.4s remaining:    0.0s
[CV] criterion=gini, n_estimators=1000 ...............................
[CV] ...... criterion=gini, n_estimators=1000, score=0.918814 -   1.6s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    4.2s remaining:    0.0s
[CV] criterion=gini, n_estimators=1000 ............

[CV] ... criterion=entropy, n_estimators=2500, score=0.932990 -   4.2s
[Parallel(n_jobs=1)]: Done  38 out of  38 | elapsed:  2.6min remaining:    0.0s
[CV] criterion=entropy, n_estimators=2500 ............................
[CV] ... criterion=entropy, n_estimators=2500, score=0.953488 -   4.3s
[Parallel(n_jobs=1)]: Done  39 out of  39 | elapsed:  2.7min remaining:    0.0s
[CV] criterion=entropy, n_estimators=3000 ............................
[CV] ... criterion=entropy, n_estimators=3000, score=0.918814 -   5.1s
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:  2.8min remaining:    0.0s
[CV] criterion=entropy, n_estimators=3000 ............................
[CV] ... criterion=entropy, n_estimators=3000, score=0.934278 -   5.1s
[Parallel(n_jobs=1)]: Done  41 out of  41 | elapsed:  2.9min remaining:    0.0s
[CV] criterion=entropy, n_estimators=3000 ............................
[CV] ... criterion=entropy, n_estimators=3000, score=0.952196 -   5.1s
[Parallel(n_jobs=1)]: Done  42 out of  42

In [178]:
clf6.best_params_

{'criterion': 'entropy', 'n_estimators': 500}

In [179]:
clf6.best_score_

0.9363714531384351

In [181]:
param_grid = [{'C':[0.001, 0.01, 0.1, 1, 10, 100, 1000], 'penalty' :["l1"], 'solver' :["liblinear"] },
                  {'C':[0.001, 0.01, 0.1, 1, 10, 100, 1000], 'penalty' :["l2"], 'solver' :[ "newton-cg", "lbfgs", "sag"] }]

clf7 = GridSearchCV(LogisticRegression(), param_grid, scoring=accu, verbose=100)
clf7.fit(train_X, train_y)
df6=pd.DataFrame(clf7.grid_scores_)

Fitting 3 folds for each of 28 candidates, totalling 84 fits
[CV] C=0.001, penalty=l1, solver=liblinear ...........................
[CV] .. C=0.001, penalty=l1, solver=liblinear, score=0.448454 -   0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[CV] C=0.001, penalty=l1, solver=liblinear ...........................
[CV] .. C=0.001, penalty=l1, solver=liblinear, score=0.448454 -   0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[CV] C=0.001, penalty=l1, solver=liblinear ...........................
[CV] .. C=0.001, penalty=l1, solver=liblinear, score=0.448320 -   0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[CV] C=0.01, penalty=l1, solver=liblinear ............................
[CV] ... C=0.01, penalty=l1, solver=liblinear, score=0.912371 -   0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[CV] C=0.01, penalty=l1, solver=liblinear .........

[CV] .......... C=0.1, penalty=l2, solver=sag, score=0.963824 -   0.0s
[Parallel(n_jobs=1)]: Done  48 out of  48 | elapsed:    0.3s remaining:    0.0s
[CV] C=1, penalty=l2, solver=newton-cg ...............................
[CV] ...... C=1, penalty=l2, solver=newton-cg, score=0.935567 -   0.0s
[Parallel(n_jobs=1)]: Done  49 out of  49 | elapsed:    0.3s remaining:    0.0s
[CV] C=1, penalty=l2, solver=newton-cg ...............................
[CV] ...... C=1, penalty=l2, solver=newton-cg, score=0.935567 -   0.0s
[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:    0.4s remaining:    0.0s
[CV] C=1, penalty=l2, solver=newton-cg ...............................
[CV] ...... C=1, penalty=l2, solver=newton-cg, score=0.963824 -   0.0s
[Parallel(n_jobs=1)]: Done  51 out of  51 | elapsed:    0.4s remaining:    0.0s
[CV] C=1, penalty=l2, solver=lbfgs ...................................
[CV] .......... C=1, penalty=l2, solver=lbfgs, score=0.935567 -   0.0s
[Parallel(n_jobs=1)]: Done  52 out of  52

In [184]:
clf7.best_params_

{'C': 1, 'penalty': 'l1', 'solver': 'liblinear'}

In [186]:
clf7.best_score_

0.9453998280309545